In [1]:
import pyntcloud
import pickle
import tensorflow as tf
import numpy as np
import importlib
from train import provider
from train import box_util

/opt/conda/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: compiletime version 3.5 of module 'tensorflow.python.framework.fast_tensor_util' does not match runtime version 3.6
  return f(*args, **kwds)
/opt/conda/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
importlib.reload(box_util)
importlib.reload(provider)

<module 'train.provider' from '/datasets/home/90/490/scgullap/ece_285_proj/frustum-pointnets/train/provider.py'>

In [3]:
NUM_POINT=2048
TRAIN_DATASET = provider.FrustumDataset(npoints=NUM_POINT, split='train',\
                            rotate_to_center=True, random_flip=False, random_shift=False, one_hot=True)

In [4]:
VAL_DATASET = provider.FrustumDataset(npoints=NUM_POINT, split='val',\
                            rotate_to_center=True, random_flip=False, random_shift=False, one_hot=True)

In [5]:
len(TRAIN_DATASET)

73480

In [6]:
TRAIN_DATASET.get_center_view_box3d(1)

array([[ 0.63603565,  1.47      ,  8.95986384],
       [ 0.7288103 ,  1.47      ,  8.48891494],
       [-0.44856195,  1.47      ,  8.25697831],
       [-0.5413366 ,  1.47      ,  8.72792721],
       [ 0.63603565, -0.42      ,  8.95986384],
       [ 0.7288103 , -0.42      ,  8.48891494],
       [-0.44856195, -0.42      ,  8.25697831],
       [-0.5413366 , -0.42      ,  8.72792721]])

In [7]:
def indices(window_len, stride_len, point_set, labels, corners_gt):
    IOU = []
    start = []
    end = []
    IOU_1 = []
    IOU_2 = []
    corner = []
    j = np.min(point_set,0)[2]
    i = j+window_len
    idtuple=set()
    while i<=np.max(point_set,0)[2]:
            max_ind = np.searchsorted(point_set[:,2], i)
            min_ind = np.searchsorted(point_set[:,2], j)
            if (min_ind,max_ind) not in idtuple and max_ind-min_ind>5:
                #print('fgbd')
                idtuple.add((min_ind,max_ind))
                labels_window = np.zeros_like(point_set[:,0])
                labels_window[min_ind:max_ind] = 1.0
                union = np.sum(np.logical_or(labels, labels_window))
                inter = np.sum(np.logical_and(labels, labels_window))
                if (inter*1.0/union) < 0.3 or (inter*1.0/union) >0.7 :
                    end.append(max_ind)
                    start.append(min_ind)
                    IOU.append(inter*1.0/union)
            j = j+stride_len
            i = j+window_len
    IOU = np.array(IOU)>=0.7
    return np.array(start),np.array(end), np.array(IOU)



In [8]:
# points in each window:2048
# number of windows
#

def get_list(start_idx,end_idx,num_points=1024,ensure_all=True):
    """
    param:
    start_idx  : list of indexes of the starting point in each window
    end_idx    : list of indees of ending point in each window
    NOTES: we used two lists because we ran into issues with tensorflow when we used tuples,
           this is a quick hack to avoid that
    num_points : number of points to be sampled from i.e number of points in each window
    ensure_all : in the case that there are fewwer than required points ensures all points are picked atleast once if selected as True
    
    
    returns:
    out:  an array of size 
          
          num_windowsxnum_pointsx1
          
          this will be used inside tensorflow to divide into windows 
          after we pass the points trough pointnet
    """
    
    out= []
    for i in range(np.shape(start_idx)[0]):
        
        if end_idx[i]-start_idx[i]+1<=num_points:
            indexes=np.arange(start_idx[i],end_idx[i])
            indexes2=np.random.choice(indexes, num_points-np.shape(indexes)[0],replace=True)
            indexes=np.concatenate((indexes,indexes2))
        else:
            indexes=np.random.choice(np.arange(start_idx[i],end_idx[i]),num_points,replace=False)
        out.append(np.reshape(indexes,(-1,1)))
    
    return np.array(out)


In [9]:
import tf_util #for conv2d
from model_util import NUM_HEADING_BIN, NUM_SIZE_CLUSTER, NUM_OBJECT_POINT
from model_util import point_cloud_masking, get_center_regression_net
from model_util import placeholder_inputs, parse_output_to_tensors, get_loss
from model_util import huber_loss

In [10]:
# https://github.com/ailias/Focal-Loss-implement-on-Tensorflow/blob/master/focal_loss.py


from tensorflow.python.ops import array_ops

def focal_loss(sigmoid_p, target_tensor, weights=None, alpha=0.99, gamma=2):
    r"""Compute focal loss for predictions.
        Multi-labels Focal loss formula:
            FL = -alpha * (z-p)^gamma * log(p) -(1-alpha) * p^gamma * log
            (1-p)
                 ,which alpha = 0.25, gamma = 2, p = sigmoid(x), z = target_tensor.
    Args:
     prediction_tensor: A float tensor of shape [batch_size, num_anchors,
        num_classes] representing the predicted logits for each class
     target_tensor: A float tensor of shape [batch_size, num_anchors,
        num_classes] representing one-hot encoded classification targets
     weights: A float tensor of shape [batch_size, num_anchors]
     alpha: A scalar tensor for focal loss alpha hyper-parameter
     gamma: A scalar tensor for focal loss gamma hyper-parameter
    Returns:
        loss: A (scalar) tensor representing the value of the loss function
    """
    #sigmoid_p = tf.nn.sigmoid(prediction_tensor)
    zeros = array_ops.zeros_like(target_tensor, dtype=target_tensor.dtype)
    
    # For poitive prediction, only need consider front part loss, back part is 0;
    # target_tensor > zeros <=> z=1, so poitive coefficient = z - p.
    pos_p_sub = array_ops.where(target_tensor > zeros, target_tensor - sigmoid_p, zeros)
    
    # For negative prediction, only need consider back part loss, front part is 0;
    # target_tensor > zeros <=> z=1, so negative coefficient = 0.
    neg_p_sub = array_ops.where(target_tensor > zeros, zeros, sigmoid_p)
    per_entry_cross_ent = - alpha * (pos_p_sub ** gamma) * tf.log(tf.clip_by_value(sigmoid_p, 1e-8, 1.0)) \
                          - (1.0 - alpha) * (neg_p_sub ** gamma) * tf.log(tf.clip_by_value(1.0 - sigmoid_p, 1e-8, 1.0))
    return tf.reduce_sum(per_entry_cross_ent)

In [11]:
# def classification_net(point_cloud, label_out_5, label_out_1, label_out_2, label_out_3, label_out_4, idx5, idx1, idx2, idx3, idx4, 
#                             is_training=True, bn_decay=True):
def classification_net(point_cloud, label_out_5,  idx5, 
                            is_training=True, bn_decay=True):
    '''
    3D PointNet network.
    param:
    
    point_cloud: TF tensor in shape (1,N,4)
                 frustum point clouds with XYZ and intensity in point channels
                 XYZs are in frustum coordinate
    label_out: TF tensor in shape (1,1)
            length-1 vector indicating the classification as car or background
    
    ??????????????????????????????????????????????????????????????????????????????????????
    
    is_training: TF boolean scalar
    bn_decay: TF float scalar
    end_points: dict                 SHOULD CHANGE THIS
    Output:                                         
    logits: TF tensor in shape (B,N,2), scores for bkg/clutter and object
    end_points: dict
    ??????????????????????????????????????????????????????????????????????????????????????
    '''
    
    batch_size = point_cloud.get_shape()[0].value #1 in our case
    num_point = point_cloud.get_shape()[1].value  #N in our case
  
    net = tf.expand_dims(point_cloud, 2)
    #print(net.get_shape())

    net = tf_util.conv2d(net, 64, [1,1],
                         padding='VALID', stride=[1,1],
                         bn=True, is_training=is_training,
                         scope='conv1', bn_decay=bn_decay)
    net = tf_util.conv2d(net, 64, [1,1],
                         padding='VALID', stride=[1,1],
                         bn=True, is_training=is_training,
                         scope='conv2', bn_decay=bn_decay)
    point_feat = tf_util.conv2d(net, 64, [1,1],
                         padding='VALID', stride=[1,1],
                         bn=True, is_training=is_training,
                         scope='conv3', bn_decay=bn_decay)
    net = tf_util.conv2d(point_feat, 128, [1,1],
                         padding='VALID', stride=[1,1],
                         bn=True, is_training=is_training,
                         scope='conv4', bn_decay=bn_decay)
    features = tf_util.conv2d(net, 1024, [1,1],
                         padding='VALID', stride=[1,1],
                         bn=True, is_training=is_training,
                         scope='conv5', bn_decay=bn_decay)
    
    features=tf.squeeze(features,axis=2)
    features=tf.squeeze(features,axis=0)   

    #features=tf.placeholder(tf.float32,[1,1024,4])

    def fn(x):
        return tf.gather_nd(features,x)
    
    windows_5 =tf.map_fn(fn,idx5,dtype=tf.float32)
#     windows_1 = tf.map_fn(fn,idx1,dtype=tf.float32)
#     windows_2 = tf.map_fn(fn,idx2,dtype=tf.float32)
#     windows_3 = tf.map_fn(fn,idx3,dtype=tf.float32)
#     windows_4 = tf.map_fn(fn,idx4,dtype=tf.float32)
    
    windows_5_1024 = tf.reduce_max(windows_5,axis=1)
#     windows_1_1024 = tf.reduce_max(windows_1,axis=1)
#     windows_2_1024 = tf.reduce_max(windows_2,axis=1)
#     windows_3_1024 = tf.reduce_max(windows_3,axis=1)
#     windows_4_1024 = tf.reduce_max(windows_4,axis=1)
    
    
    winex_5 =  tf.reshape(windows_5_1024,shape=[-1,1,1,1024])
#     winex_1 =  tf.reshape(windows_1_1024,shape=[-1,1,1,1024])
#     winex_2 =  tf.reshape(windows_2_1024,shape=[-1,1,1,1024])
#     winex_3 =  tf.reshape(windows_3_1024,shape=[-1,1,1,1024])
#     winex_4 =  tf.reshape(windows_4_1024,shape=[-1,1,1,1024])
   
    winex = tf.concat([winex_5], axis=0)
    label_out = tf.concat([label_out_5],axis=0)

    
    
#     winex = tf.concat([winex_5, winex_1, winex_2, winex_3, winex_4], axis=0)
#     label_out = tf.concat([label_out_5,label_out_1, label_out_2, label_out_3, label_out_4],axis=0)

    #classification head
    d1 = tf_util.conv2d(winex, 512, [1,1],
                             padding='VALID', stride=[1,1],
                             bn=True, is_training=is_training,
                             scope='dense1', bn_decay=bn_decay)
    d2 = tf_util.conv2d(d1, 256, [1,1],
                             padding='VALID', stride=[1,1],
                             bn=True, is_training=is_training,
                             scope='dense2', bn_decay=bn_decay)
    d2=tf.layers.dropout(d2,rate=0.5, training=is_training, name='drop1')
    
    logits = tf_util.conv2d(d2, 1, [1,1],
                             padding='VALID', stride=[1,1],
                             bn=True, is_training=is_training,
                             scope='out', bn_decay=bn_decay, activation_fn=None)
    
    logits = tf.squeeze(logits)
    logits=tf.reshape(tf.squeeze(logits),(1,-1))
    sig = tf.sigmoid(logits)

    #sig = tf.reshape(tf.squeeze(sig),(-1,1))
    y=tf.reshape(sig,[-1])
    
    max_ind = tf.argmax(y)
    
    tp = tf.equal(label_out[max_ind], 1)
    
    
    differentiable_round = tf.maximum(y-0.499,0)
    differentiable_round = differentiable_round * 10000
    y_pred = tf.minimum(differentiable_round, 1)
    #y_pred=tf.round(y)
    
    true_pos  = tf.reduce_sum(tf.cast(tf.logical_and(tf.cast(label_out,tf.bool),tf.cast(y_pred,tf.bool)),tf.float32))
    
    false_pos = tf.reduce_sum(tf.cast(tf.logical_and(tf.logical_not(tf.cast(label_out,tf.bool)),tf.cast(y_pred,tf.bool)),tf.float32))
    true_neg  = tf.reduce_sum(tf.cast(tf.logical_not(tf.logical_or(tf.cast(label_out, tf.bool),\
                                                                   tf.cast(y_pred, tf.bool))),tf.float32))
    false_neg = tf.reduce_sum(tf.cast(tf.logical_and(tf.logical_not\
                                                     (tf.cast(y_pred,tf.bool)),tf.cast(label_out,tf.bool)),tf.float32))
    return sig,logits, label_out,true_pos,false_pos,true_neg,false_neg, tp, max_ind

In [12]:
# inputs=tf.placeholder(tf.float32,[None,2048,4])
# idx_5 =tf.placeholder(tf.int32,[None,num_points_5,1])
# is_training = tf.placeholder(tf.bool)
# label_out_5 = tf.placeholder(tf.int32, [None])

In [13]:
tf.reset_default_graph()
with tf.device('/device:GPU:0'):
    num_points_5 =512
#     num_points_1 = 512
#     num_points_2 = 512
#     num_points_3 = 512
#     num_points_4 = 512
    
    inputs=tf.placeholder(tf.float32,[None,2048,4])#put placeholder

    idx_5 =tf.placeholder(tf.int32,[None,num_points_5,1])

#     idx_1 = tf.placeholder(tf.int32,[None,num_points_1,1])
    
#     idx_2 = tf.placeholder(tf.int32,[None,num_points_2,1])

#     idx_3 = tf.placeholder(tf.int32,[None,num_points_3,1])
    
#     idx_4 = tf.placeholder(tf.int32,[None,num_points_4,1])

    is_training = tf.placeholder(tf.bool)
    

    label_out_5 = tf.placeholder(tf.int32, [None])
#     label_out_1 = tf.placeholder(tf.int32, [None])
#     label_out_2 = tf.placeholder(tf.int32, [None])
#     label_out_3 = tf.placeholder(tf.int32, [None])
#     label_out_4 = tf.placeholder(tf.int32, [None])

    sig,logits, label_out,tp,fp,tn,fn, tp_num, maxi = classification_net(inputs, label_out_5, \
                                         idx_5, is_training)
    
    
#     sig,logits, label_out,tp,fp,tn,fn = classification_net(inputs, label_out_5, label_out_1,label_out_2, label_out_3, label_out_4, \
#                                          idx_5, idx_1, idx_2, idx_3, idx_4, is_training)
    
    func_fl = focal_loss(tf.squeeze(sig),tf.squeeze(tf.cast(label_out, tf.float32)), gamma=0.75, alpha=0.25)
    print(label_out.get_shape())
#     loss=tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(
#     labels=tf.reshape(tf.cast(label_out,tf.float32),(-1,1)),
#     logits=tf.reshape(logits,(-1,1))))

    loss = tf.reduce_mean(func_fl)
#     tpr=tf.divide(tf.cast(tp,tf.float32),tf.add(tp,fp))
#     tnr=tf.divide(tf.cast(tn,tf.float32),tf.add(tn,fn))
#     loss=tf.reduce_sum(tf.constant(1.0)-tf.scalar_mul(0.5,tf.add(tpr,tnr)))
    
    
    optimizer = tf.train.AdamOptimizer(1e-5)
    #train_step=optimizer.minimize(loss)
    update_ops = tf.get_collection(tf.GraphKeys.UPDATE_OPS)
    with tf.control_dependencies(update_ops):
        train_op = optimizer.minimize(loss)
    
    

(?,)


In [14]:
trix = np.load('./Windows/trix.npy')

In [15]:
trix=list(trix)

In [ ]:
import datetime
import logging
from random import shuffle
#logging.basicConfig(filename='run_1.log',level=logging.DEBUG)
from tensorflow.python import debug as tf_debug
print(datetime.datetime.now().strftime("%a, %d %B %Y %I:%M:%S"))

IOU_list = []
saver = tf.train.Saver()
trix=[cc for cc in range(TRAIN_DATASET.__len__())]
shuffle(trix)
prob = []
with tf.Session(config=tf.ConfigProto(allow_soft_placement=True, log_device_placement=True)) as sess:
    #sess=tf_debug.LocalCLIDebugWrapperSession(sess)
    sess.run(tf.global_variables_initializer())
    variables_names = [v.name for v in tf.trainable_variables()]
    values = sess.run(variables_names)
    for k, v in zip(variables_names, values):
        print("Variable: ", k)
        print("Shape: ", v.shape)
    # uncomment this when we want to load the checkpoint model
    #saver.restore(sess, "./checkpoints/model_new_labels_pointwiseIOU_5_10000.ckpt")

    
    for j in range(0,15):   
        total_tp=0
        total_fp=0
        total_tn=0
        total_fn=0
        total_tpnums = 0
        total_fpnums = 0
        total_fnnums = 0
        
        
        print(datetime.datetime.now().strftime("%a, %d %B %Y %I:%M:%S"))
        
        print('Epoch Number........................................',j)
        pedc=0
        
        for i in trix:
        #todo reformat code to have lists instead of many variable
            if TRAIN_DATASET.type_list[i]=='Pedestrian':
                pedc+=1
                if pedc%500==0:
                    total_tp=0
                    total_fp=0
                    total_tn=0
                    total_fn=0
                    total_tpnums = 0
                    total_fpnums = 0
                    total_fnnums = 0
                point_set,labels,a,b,c,d,e,f,cls = TRAIN_DATASET.__getitem__(i)

                index = np.argsort(point_set[:,2])
                point_set = point_set[index]
                labels = labels[index]

                corners_gt = TRAIN_DATASET.get_center_view_box3d(i)
                
 
                s5,e5,l = indices(1.0,0.1,point_set,labels, corners_gt)
        
                #l1 = (l1>=0.6)
                
                print('Label shape', l.shape)


                if s5.size :#and s2.size and s3.size and s4.size and s1.size:

                    ind_5 = get_list(s5,e5, num_points=512)



                    point_set = np.expand_dims(point_set, axis=0)
                        
                    _, x,tpos,fpos,tneg,fneg, tpnums, maxind =sess.run([train_op, loss,tp,fp,tn,fn, tp_num, maxi],feed_dict={idx_5:ind_5,\
                                                               label_out_5: l.astype(np.int32),\
                                                               inputs:point_set, is_training: True})
                    total_tp+=tpos
                    total_fp+=fpos
                    total_tn+=tneg
                    total_fn+=fneg
                    total_tpnums+= tpnums
                    total_fpnums+= (1-tpnums)
                    total_fnnums+= (1-tpnums)
                    ind_5[maxind]
                    print('----------------------------------------------------------------------------------')
                    print('Epoch ', j , 'Loss for the current example ',i,' = ', x,'pedc = ',pedc)
                    #logging.info('Loss for the current example ',i,' = ', x)
                    print('Metrics for current example: TP=',tpos,' FP=',fpos,' TN=',tneg,' FN=',fneg)
                    #logging.info('Metrics for current example: TP=',tpos,' FP=',fpos,' TN=',tneg,' FN=',fneg)  # will not print anything
                    #print('Cumulative metrics: TP=',total_tp,' FP=',total_fp,' TN=',total_tn,' FN=',total_fn)
                    print('Cumulative metrics: Precision = ',(total_tp*1.0)/(total_tp+total_fp),\
                          ' Recall = ',(total_tp*1.0)/(total_tp+total_fn))
                    #logging.info('Cumulative metrics: Precision = ',(total_tp*1.0)/(total_tp+total_fp),\
                    #      ' Recall = ',(total_tp*1.0)/(total_tp+total_fn))
                    print('Single metrics: Precision = ',(total_tpnums*1.0)/(total_tpnums+total_fpnums),\
                          ' Recall = ',(total_tpnums*1.0)/(total_tpnums+total_fnnums))
                    print('----------------------------------------------------------------------------------')
                    
                    if(pedc%5000==0):
                        save_path = saver.save(sess, "./checkpoints/final_pointwiseIOU_"+str(j)+'_'+str(pedc)+".ckpt")
                    

                #print(c)
                #print(n)
            #i += 1
        #-----------------------------------------------------------------------------------------------#
        print('&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&')
        k = 0
        Vtotal_tp=0
        Vtotal_fp=0
        Vtotal_tn=0
        Vtotal_fn=0
        Vtotal_tpnums = 0
        Vtotal_fpnums = 0
        Vtotal_fnnums = 0
        while k<len(VAL_DATASET):
        #todo reformat code to have lists instead of many variable

            if VAL_DATASET.type_list[k]=='Pedestrian':

                point_set,labels,a,b,c,d,e,f,cls = VAL_DATASET.__getitem__(k)

                index = np.argsort(point_set[:,2])
                point_set = point_set[index]
                labels = labels[index]

                
                corners_gt = VAL_DATASET.get_center_view_box3d(k)
                
                #print(point_set.shape)

                s5,e5,l = indices(1.0,0.1,point_set,labels, corners_gt)
                
                #l1 = l1>0.5

#                 s1, e1, l1 = indices(k, 1.1, 0.2, 'val')

#                 s2, e2, l2 = indices(k, 1.3, 0.2, 'val')

#                 s3, e3, l3 = indices(k, 0.7, 0.1, 'val')

#                 s4, e4, l4 = indices(k, 0.5, 0.1, 'val')

                if s5.size :#and s2.size and s3.size and s4.size and s1.size:

                    ind_5 = get_list(s5,e5, num_points=512)

#                     ind_1 = get_list(s1,e1, num_points=512)

#                     ind_2 = get_list(s2,e2, num_points=512)

#                     ind_3 = get_list(s3,e3, num_points=512)

#                     ind_4 = get_list(s4,e4, num_points=512)

#                     t_windows=s1.shape[0]+s2.shape[0]+s3.shape[0]+s4.shape[0]+s5.shape[0]

                    point_set = np.expand_dims(point_set, axis=0)
                    print(Vtotal_tp)
                    x,tpos,fpos,tneg,fneg, tp_nums, maxind =sess.run([loss,tp,fp,tn,fn, tp_num, maxi],feed_dict={idx_5:ind_5, \
                                                               label_out_5: l.astype(np.int32), inputs:point_set, is_training: True})


                    #window_points = ind_5[maxind]

                    #window_points = point_set[0,ind_5[maxind].reshape((-1))][:,:3]
                    #min_x, min_y, min_z = np.min(window_points,axis=0)
                    #max_x, max_y, max_z = np.max(window_points,axis=0)
                    #corners = [[min_x,max_y,max_z],[min_x,max_y,min_z],[max_x,max_y,min_z],[max_x,max_y,max_z],\
                    #           [min_x,min_y,max_z],[min_x,min_y,min_z],[max_x,min_y,min_z],[max_x,min_y,max_z]]
                    #corners=np.array(corners)
                    #corners_gt = VAL_DATASET.get_center_view_box3d(k)
                    #IOU, IOU_2D, inter, inter_vol = box_util.box3d_iou(corners, corners_gt)
                    #print('IOUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUUU')
                    #print(IOU, IOU_2D, inter, inter_vol)
                    #IOU_list.append([IOU, IOU_2D, inter, inter_vol, k])
                    #if inter>0.4:
                    #    c += 1
                    #    if inter>0.5:
                    #        c1 += 1
                    #if inter_vol>0.4:
                    #    c2 += 1
                    #    if inter_vol>0.5:
                    #        c3 +=1 

                    print(Vtotal_tp)
                    Vtotal_tp +=tpos
                    Vtotal_fp +=fpos
                    Vtotal_tn +=tneg
                    Vtotal_fn +=fneg
                    Vtotal_tpnums+= tp_nums
                    Vtotal_fpnums+= (1-tp_nums)
                    Vtotal_fnnums+= (1-tp_nums)
                    print('&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&')
                    print('Epoch ', j , 'Loss for the current example ',k,' = ', x)
                    #logging.info('Loss for the current example ',i,' = ', x)
                    print('Metrics for current example: TP=',tpos,' FP=',fpos,' TN=',tneg,' FN=',fneg)
                    #logging.info('Metrics for current example: TP=',tpos,' FP=',fpos,' TN=',tneg,' FN=',fneg)  # will not print anything
                    #print('Cumulative metrics: TP=',total_tp,' FP=',total_fp,' TN=',total_tn,' FN=',total_fn)
                    print('Cumulative metrics: Precision = ',(Vtotal_tp*1.0)/(Vtotal_tp+Vtotal_fp),\
                          ' Recall = ',(Vtotal_tp*1.0)/(Vtotal_tp+Vtotal_fn))

                    print('Single metrics: Precision = ',(Vtotal_tpnums*1.0)/(Vtotal_tpnums+Vtotal_fpnums),\
                          ' Recall = ',(Vtotal_tpnums*1.0)/(Vtotal_tpnums+Vtotal_fnnums))
                    #logging.info('Cumulative metrics: Precision = ',(Vtotal_tp*1.0)/(Vtotal_tp+Vtotal_fp),\
                    #      ' Recall = ',(Vtotal_tp*1.0)/(Vtotal_tp+Vtotal_fn))
                    print('&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&')

            k += 1

        #----------------------------------------------------------------------------------------------#
#         prob = sess.run([sig],feed_dict={idx_5:ind_5, idx_1:ind_1, idx_2:ind_2, idx_3:ind_3, idx_4:ind_4,\
#                                                        label_out_5: l5.astype(np.int32), label_out_1: l1.astype(np.int32),\
#                                                        label_out_2: l2.astype(np.int32), label_out_3: l3.astype(np.int32),\
#                                                        label_out_4: l4.astype(np.int32), inputs:point_set,  is_training: False})
#         print(prob)
        print(ind_5)
        print(label_out_5)
        prob = sess.run([sig],feed_dict={idx_5:ind_5,  \
                                                       label_out_5: l.astype(np.int32), inputs:point_set,  is_training: True})
        print(prob)
print(datetime.datetime.now().strftime("%a, %d %B %Y %I:%M:%S") )

Mon, 11 June 2018 01:03:40
Variable:  conv1/weights:0
Shape:  (1, 1, 4, 64)
Variable:  conv1/biases:0
Shape:  (64,)
Variable:  conv1/bn/beta:0
Shape:  (64,)
Variable:  conv1/bn/gamma:0
Shape:  (64,)
Variable:  conv2/weights:0
Shape:  (1, 1, 64, 64)
Variable:  conv2/biases:0
Shape:  (64,)
Variable:  conv2/bn/beta:0
Shape:  (64,)
Variable:  conv2/bn/gamma:0
Shape:  (64,)
Variable:  conv3/weights:0
Shape:  (1, 1, 64, 64)
Variable:  conv3/biases:0
Shape:  (64,)
Variable:  conv3/bn/beta:0
Shape:  (64,)
Variable:  conv3/bn/gamma:0
Shape:  (64,)
Variable:  conv4/weights:0
Shape:  (1, 1, 64, 128)
Variable:  conv4/biases:0
Shape:  (128,)
Variable:  conv4/bn/beta:0
Shape:  (128,)
Variable:  conv4/bn/gamma:0
Shape:  (128,)
Variable:  conv5/weights:0
Shape:  (1, 1, 128, 1024)
Variable:  conv5/biases:0
Shape:  (1024,)
Variable:  conv5/bn/beta:0
Shape:  (1024,)
Variable:  conv5/bn/gamma:0
Shape:  (1024,)
Variable:  dense1/weights:0
Shape:  (1, 1, 1024, 512)
Variable:  dense1/biases:0
Shape:  (512,)


Label shape (65,)
----------------------------------------------------------------------------------
Epoch  0 Loss for the current example  58270  =  19.979902 pedc =  16
Metrics for current example: TP= 6.0  FP= 26.0  TN= 33.0  FN= 0.0
Cumulative metrics: Precision =  0.12462006079027356  Recall =  0.5942028985507246
Single metrics: Precision =  0.125  Recall =  0.125
----------------------------------------------------------------------------------
Label shape (49,)
----------------------------------------------------------------------------------
Epoch  0 Loss for the current example  7725  =  15.599133 pedc =  17
Metrics for current example: TP= 8.0  FP= 16.0  TN= 24.0  FN= 1.0
Cumulative metrics: Precision =  0.1388101983002833  Recall =  0.6282051282051282
Single metrics: Precision =  0.11764705882352941  Recall =  0.11764705882352941
----------------------------------------------------------------------------------
Label shape (90,)
----------------------------------------------

Label shape (56,)
----------------------------------------------------------------------------------
Epoch  0 Loss for the current example  42367  =  20.843275 pedc =  34
Metrics for current example: TP= 3.0  FP= 26.0  TN= 27.0  FN= 0.0
Cumulative metrics: Precision =  0.11149032992036405  Recall =  0.7313432835820896
Single metrics: Precision =  0.2647058823529412  Recall =  0.2647058823529412
----------------------------------------------------------------------------------
Label shape (17,)
----------------------------------------------------------------------------------
Epoch  0 Loss for the current example  57081  =  6.3157396 pedc =  35
Metrics for current example: TP= 1.0  FP= 5.0  TN= 11.0  FN= 0.0
Cumulative metrics: Precision =  0.11186440677966102  Recall =  0.7333333333333333
Single metrics: Precision =  0.2571428571428571  Recall =  0.2571428571428571
----------------------------------------------------------------------------------
Label shape (11,)
---------------------

----------------------------------------------------------------------------------
Epoch  0 Loss for the current example  19616  =  15.50997 pedc =  52
Metrics for current example: TP= 0.0  FP= 18.0  TN= 19.0  FN= 0.0
Cumulative metrics: Precision =  0.11462160176340926  Recall =  0.7839195979899497
Single metrics: Precision =  0.3076923076923077  Recall =  0.3076923076923077
----------------------------------------------------------------------------------
Label shape (40,)
----------------------------------------------------------------------------------
Epoch  0 Loss for the current example  30095  =  11.434369 pedc =  53
Metrics for current example: TP= 5.0  FP= 14.0  TN= 21.0  FN= 0.0
Cumulative metrics: Precision =  0.11666666666666667  Recall =  0.7892156862745098
Single metrics: Precision =  0.32075471698113206  Recall =  0.32075471698113206
----------------------------------------------------------------------------------
Label shape (185,)
------------------------------------

Label shape (72,)
----------------------------------------------------------------------------------
Epoch  0 Loss for the current example  49763  =  24.706818 pedc =  71
Metrics for current example: TP= 4.0  FP= 26.0  TN= 42.0  FN= 0.0
Cumulative metrics: Precision =  0.12384573601303639  Recall =  0.8290909090909091
Single metrics: Precision =  0.4084507042253521  Recall =  0.4084507042253521
----------------------------------------------------------------------------------
Label shape (73,)
----------------------------------------------------------------------------------
Epoch  0 Loss for the current example  38736  =  26.830967 pedc =  72
Metrics for current example: TP= 2.0  FP= 31.0  TN= 40.0  FN= 0.0
Cumulative metrics: Precision =  0.12273212379935966  Recall =  0.8303249097472925
Single metrics: Precision =  0.4166666666666667  Recall =  0.4166666666666667
----------------------------------------------------------------------------------
Label shape (15,)
--------------------

...

7055.0
7055.0
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
Epoch  0 Loss for the current example  12876  =  5.638671
Metrics for current example: TP= 8.0  FP= 5.0  TN= 21.0  FN= 0.0
Cumulative metrics: Precision =  0.33667000333667  Recall =  0.9770369345690967
Single metrics: Precision =  0.8694714131607335  Recall =  0.8694714131607335
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
7063.0
7063.0
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
Epoch  0 Loss for the current example  12896  =  22.970766
Metrics for current example: TP= 8.0  FP= 14.0  TN= 79.0  FN= 0.0
Cumulative metrics: Precision =  0.33669825246416835  Recall =  0.9770623186403206
Single metrics: Precision =  0.8695417789757413  Recall =  0.8695417789757413
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
7071.

7132.0
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
Epoch  0 Loss for the current example  12987  =  3.6172342
Metrics for current example: TP= 4.0  FP= 0.0  TN= 21.0  FN= 0.0
Cumulative metrics: Precision =  0.33751123303220926  Recall =  0.9772665023281293
Single metrics: Precision =  0.8701229289150187  Recall =  0.8701229289150187
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
7136.0
7136.0
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
Epoch  0 Loss for the current example  13015  =  17.878126
Metrics for current example: TP= 0.0  FP= 13.0  TN= 36.0  FN= 0.0
Cumulative metrics: Precision =  0.33730383815466064  Recall =  0.9772665023281293
Single metrics: Precision =  0.8696581196581197  Recall =  0.8696581196581197
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
7136.0
7

7184.0
7184.0
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
Epoch  0 Loss for the current example  13223  =  10.384161
Metrics for current example: TP= 6.0  FP= 3.0  TN= 36.0  FN= 0.0
Cumulative metrics: Precision =  0.3371787657099981  Recall =  0.9767694606711045
Single metrics: Precision =  0.8691737288135594  Recall =  0.8691737288135594
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
7190.0
7190.0
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
Epoch  0 Loss for the current example  13225  =  15.769991
Metrics for current example: TP= 3.0  FP= 8.0  TN= 47.0  FN= 0.0
Cumulative metrics: Precision =  0.3371455355050387  Recall =  0.9767789244975557
Single metrics: Precision =  0.8692429857067231  Recall =  0.8692429857067231
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
7193

7258.0
7258.0
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
Epoch  0 Loss for the current example  13305  =  22.780518
Metrics for current example: TP= 9.0  FP= 8.0  TN= 96.0  FN= 0.0
Cumulative metrics: Precision =  0.3362795002313744  Recall =  0.9770099489109976
Single metrics: Precision =  0.869884575026233  Recall =  0.869884575026233
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
7267.0
7267.0
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
Epoch  0 Loss for the current example  13306  =  30.027113
Metrics for current example: TP= 6.0  FP= 15.0  TN= 110.0  FN= 0.0
Cumulative metrics: Precision =  0.3362304100596366  Recall =  0.9770284793121977
Single metrics: Precision =  0.869952805453592  Recall =  0.869952805453592
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
7273.0

7325.0
7325.0
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
Epoch  0 Loss for the current example  13346  =  13.3720665
Metrics for current example: TP= 3.0  FP= 8.0  TN= 51.0  FN= 0.0
Cumulative metrics: Precision =  0.3355925993771753  Recall =  0.9771969595946126
Single metrics: Precision =  0.8695426195426196  Recall =  0.8695426195426196
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
7328.0
7328.0
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
Epoch  0 Loss for the current example  13348  =  7.795782
Metrics for current example: TP= 2.0  FP= 2.0  TN= 31.0  FN= 0.0
Cumulative metrics: Precision =  0.3356227106227106  Recall =  0.9772030395947207
Single metrics: Precision =  0.8696103896103896  Recall =  0.8696103896103896
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&
7330